# ReActNet
This notebook demonstrates the implementation of the ReActNet Paper
# Steps to binarize the model
- Load Dataset and DataLoader
- Create the teacher model to be binarized
- Load the configuration YAML file
- create `ReActNet object` and pass the teacher model, dataloader, configuration
- Binarize the model by using `compress_model` method

In [2]:
import sys
import os
import shutil
sys.path.append("../../")
sys.path.append("../../../../../")

import torch
from torchvision import transforms
from trailmet.models import ModelsFactory
from trailmet.datasets.classification import DatasetFactory
from trailmet.algorithms.binarize.utils import *
from trailmet.algorithms.binarize.ReActNet import ReActNet
from trailmet.models.models import models
import torchvision

import yaml

In [3]:
os.environ["CUDA_VISIBLE_DEVICES"]='7' 

In [4]:
root_dir = './'
import os
with open(os.path.join(root_dir,"reactnet_cifar100.yaml"),'r') as stream:
    kwargs = yaml.safe_load(stream)
dataset_args = kwargs['GENERAL']
kwargs

{'GENERAL': {'DATASET': 'c100',
  'BACKBONE': 'mobilenetv2',
  'batch_size': 256,
  'workers': 4,
  'valid_size': 0.1,
  'num_train': 0,
  'num_classes': 100,
  'insize': 32},
 'ReActNet1_ARGS': {'batch_size': 256,
  'epochs': 256,
  'learning_rate': 0.0005,
  'momentum': 0.9,
  'weight_deacy': '1e-5',
  'label_smooth': 0.1,
  'save': './save_path_mbnet_cifar100_0fp/step1'},
 'ReActNet2_ARGS': {'batch_size': 256,
  'epochs': 256,
  'learning_rate': 0.0005,
  'momentum': 0.9,
  'weight_deacy': 0,
  'label_smooth': 0.1,
  'save': './save_path_mbnet_cifar100_0fp/step2'}}

In [5]:
def set_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    os.environ['PYTHONHASHSEED'] = str(seed)
    print('> SEEDING DONE')
    
set_seed(1024)  

> SEEDING DONE


# Defining the Model 

In [6]:
model_name = 'mobilenetv2'
teacher = models.get_model('mobilenetv2', 'full', 100, 32)

pret = torch.load('/workspace/code/janhavi/ChipNet/weights/mobilenetv2_c100_pretrained.pth', map_location='cuda')
pret = pret['state_dict']

teacher.load_state_dict(pret)

<All keys matched successfully>

# Augmentation, Dataset and DataLoaders

In [9]:
# Augmentation
crop_scale = 0.08
lighting_param = 0.1
train_transform = transforms.Compose([
    transforms.RandomResizedCrop(32, scale=(crop_scale, 1.0)),
    Lighting(lighting_param),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor()])

valid_transform = transforms.Compose([
        transforms.Resize(36),
        transforms.CenterCrop(32),
        transforms.ToTensor()
    ])
test_transform = valid_transform

input_transforms = {
    'train': train_transform, 
    'val': valid_transform, 
    'test': test_transform}

target_transforms = {
    'train': None, 
    'val': None, 
    'test': None}

# Create Dataset
cifar100_dataset = DatasetFactory.create_dataset(name = 'CIFAR100', 
                                        root = root_dir,
                                        split_types = ['train', 'val', 'test'],
                                        val_fraction = 0.15,
                                        transform = input_transforms,
                                        target_transform = target_transforms
                                        )
# Define DataLoaders
train_loader100 = torch.utils.data.DataLoader(
        cifar100_dataset['train'], batch_size=dataset_args['batch_size'], 
        sampler=cifar100_dataset['train_sampler'],
        num_workers=dataset_args['workers']
    )
val_loader100 = torch.utils.data.DataLoader(
        cifar100_dataset['val'], batch_size=dataset_args['batch_size'], 
        sampler=cifar100_dataset['val_sampler'],
        num_workers=dataset_args['workers']
    )
test_loader100 = torch.utils.data.DataLoader(
        cifar100_dataset['test'], batch_size=dataset_args['batch_size'], 
        sampler=cifar100_dataset['test_sampler'],
        num_workers=dataset_args['workers']
    )

dataloaders = {
        'train': train_loader100, 'val': val_loader100, "test": test_loader100
}


Files already downloaded and verified
Files already downloaded and verified
Files already downloaded and verified


# ReActNet Object

In [ ]:
a = ReActNet(teacher, model_name, dataloaders, num_fp=0, **kwargs)

# Binarizing the model

In [ ]:
fin = a.compress_model()

Creating Logging Directory...
Step-1 Training with activations binarized for 256 epochs

12/27 01:48:27 AM Step-1 Training with activations binarized for 256 epochs

12/27 01:48:27 AM epoch, train acc, train loss, val acc, val loss
EPOCH-0

learning_rate: 0.000498046875


/opt/conda/envs/ml/lib/python3.10/site-packages/torch/optim/lr_scheduler.py:131: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "


Train: [  0/176]	Time  1.035 ( 1.035)	Loss 6.3489e+00 (6.3489e+00)	Acc@1   0.78 (  0.78)	Acc@5   5.47 (  5.47)
Train: [  1/176]	Time  0.145 ( 0.590)	Loss 5.4485e+00 (5.8987e+00)	Acc@1   2.34 (  1.56)	Acc@5   5.47 (  5.47)
Train: [  2/176]	Time  0.106 ( 0.429)	Loss 5.2554e+00 (5.6842e+00)	Acc@1   1.95 (  1.69)	Acc@5   6.64 (  5.86)
Train: [  3/176]	Time  0.116 ( 0.351)	Loss 5.4839e+00 (5.6342e+00)	Acc@1   0.78 (  1.46)	Acc@5   3.12 (  5.18)
Train: [  4/176]	Time  0.117 ( 0.304)	Loss 5.3462e+00 (5.5766e+00)	Acc@1   0.39 (  1.25)	Acc@5   5.47 (  5.23)
Train: [  5/176]	Time  0.101 ( 0.270)	Loss 5.0602e+00 (5.4905e+00)	Acc@1   1.56 (  1.30)	Acc@5   7.81 (  5.66)
Train: [  6/176]	Time  0.105 ( 0.246)	Loss 5.1022e+00 (5.4350e+00)	Acc@1   1.95 (  1.40)	Acc@5   6.64 (  5.80)
Train: [  7/176]	Time  0.124 ( 0.231)	Loss 5.1094e+00 (5.3943e+00)	Acc@1   1.95 (  1.46)	Acc@5   7.81 (  6.05)
Train: [  8/176]	Time  0.112 ( 0.218)	Loss 5.0978e+00 (5.3614e+00)	Acc@1   4.30 (  1.78)	Acc@5  13.28 (  6.86)
T

# Evaluate binarized model on test set

In [8]:
chk=torch.load('./save_path_mbnet_cifar100_0fp/step2/c100-model_best.pth.tar')

In [12]:
chk['best_top1_acc']

tensor(42.4600)